# Bijections, bijections, bijections ...

Marc Lorenzi - Février 2018

## 1. Une bijection de $\mathbb N \times \mathbb N$ vers $\mathbb N$

### 1.1 La fonction $\varphi$

La fonction $\varphi:\mathbb N \to \mathbb N$ définie par $\varphi(n)=\frac 1 2 n(n+1)$ est une injection strictement croissante.

In [ ]:
def phi(n):
    return n * (n + 1) // 2

In [ ]:
[(k, phi(k)) for k in range(11)]

Comme $\varphi(0) = 0$ et $\varphi$ est strictement croissante, pour tout entier naturel $t$ il existe un unique entier $n$ tel que $\varphi(n)\le t <\varphi(n+1)$. Cet entier $n$ peut être obtenu par dichotomie.

In [ ]:
def max_phi(t):
    a = 0
    b = t + 1
    while b - a > 1:
        c = (a + b) // 2
        if phi(c) <= t: a = c
        else: b = c
    return a

In [ ]:
max_phi(123456789)

In [ ]:
phi(15712), phi(15713)

### 1.2 La fonction $f_2$ et sa réciproque

La fonction $f_2:\mathbb N\times\mathbb N$ définie par $f_2(x,y) = \varphi(x+y) + y$ est une bijection.

In [ ]:
def f2(x, y):
    n = x + y
    return phi(n) + y

Soit $t\in\mathbb N$. Soit $n$ tel que $\varphi(n)\le t < \varphi(n+1)$. Posons alors $y=t-\varphi(n)$ et $x=n-y$. On vérifie facilement que $x,y\in\mathbb N$ et $f_2(x,y)=t$. Il est donc aisé de coder la réciproque de la fonction $f_2$.

In [ ]:
def recip_f2(t):
    n = max_phi(t)
    y = t - phi(n)
    x = n - y
    return (x, y)

In [ ]:
recip_f2(123456789)

In [ ]:
f2(251, 15461)

In [ ]:
recip_f2(10 ** 20)

In [ ]:
recip_f2(10 ** 100)

### 1.3 Tests

Un million de tests pour se convaincre que `f2` et `recip_f2` sont bien réciproques l'une de l'autre ...

In [ ]:
for t in range(10 ** 6 + 1):
    (x, y) = recip_f2(t)
    assert f2(x, y) == t
print('test 1 ok')

In [ ]:
for x in range(1001):
    for y in range(1001):
        assert recip_f2(f2(x, y)) == (x, y)
print('test 2 ok')

## 2. Une bijection de $\mathbb N^3$ vers $\mathbb N$

Ayant écrit une bijection de $\mathbb N^2$ vers $\mathbb N$, il est simple d'écrire une bijection de $\mathbb N^3$ vers $\mathbb N$, en remarquant que $\mathbb N^3$ est en bijection avec $\mathbb N\times\mathbb N^2$. Cela nous donne la fonction $f_3:\mathbb N^3\to\mathbb N$ définie par $f_3(x, y, z)=f_2(x,f_2(y, z))$.

In [ ]:
def f3(x, y, z):
    return f2(x, f2(y, z))

La réciproque de $f_3$ est facile à obtenir puisqu'on connaît celle de $f_2$.

In [ ]:
def recip_f3(t):
    (x, u) = recip_f2(t)
    (y, z) = recip_f2(u)
    return (x, y, z)

In [ ]:
f3(123, 456, 789)

In [ ]:
recip_f3(10 ** 9)

In [ ]:
f3(6280, 62, 214)

## 3. Une bijection de $\mathbb L^*$ vers $\mathbb N$

Notons $\mathbb L$ l'ensemble des listes d'entiers, et $\mathbb L^*$ l'ensemble des listes non vides d'entiers. La fonction $g$ ci-dessous prend en paramètre une liste $s$ non vide, s'appelle récursivement sur les deux moitiés de $s$ pour calculer deux entiers, et applique la fonction $f_2$ à ces deux entiers.

In [ ]:
def g(s):
    if len(s) == 1: return s[0]
    else:
        p = len(s)
        q = p // 2
        s1 = s[0:q]
        s2 = s[q:]
        return f2(g(s1), g(s2))

In [ ]:
g(range(1, 11))

Si l'on connaît la longueur de la liste $s$ passée en paramètre à $g$, on peut alors retrouver $s$ à partir de $g(s)$.

In [ ]:
def recip_g(p, t):
    if p == 1: return [t]
    else:
        U, V = recip_f2(t)
        p1 = p // 2
        p2 = p - p1
        Y = recip_g(p1, U)
        Z = recip_g(p2, V)
        return Y + Z

In [ ]:
s = recip_g(10, 10 ** 40)

In [ ]:
s

In [ ]:
g(s)

Pour parfaire le tout, en composant $g$ et $f_2$, on peut englober l'information sur la longueur de $s$ dans l'entier renvoyé par la fonction. La fonction $f$ ci-dessous est ainsi une bijection de $\mathbb L^*$ vers $\mathbb N$.

In [ ]:
def f(s):
    p = len(s)
    return f2(g(s), p - 1)

In [ ]:
f([1, 5, 2, 3])

In [ ]:
def recip_f(t):
    y, p = recip_f2(t)
    return recip_g(p + 1, y)

In [ ]:
recip_f(511569)

## 4. Une bijection de $\mathbb L$ vers $\mathbb N$

Un petit décalage permet enfin de créer une bijection $F:\mathbb L\to\mathbb N$.

In [ ]:
def F(s):
    if len(s) == 0: return 0
    else: return f(s) + 1

In [ ]:
t = F(range(11))
t

In [ ]:
def recip_F(t):
    if t == 0: return []
    else: return recip_f(t - 1)

In [ ]:
recip_F(t)

Faisons quelques tests ...

In [ ]:
import random

In [ ]:
def random_list(n):
    return [random.randint(0, 1000) for k in range(n)]

In [ ]:
random_list(10)

In [ ]:
def test(n):
    s = random_list(n)
    print('s = ', s)
    t = F(s)
    print('F(s) = ', t)
    s1 = recip_F(t)
    print('recip_F(t) = ', s1)

In [ ]:
test(15)